<a href="https://colab.research.google.com/github/xyz-zy/CaGif-/blob/master/BERT_Pytorch_SQuAD.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
!pip3 install torchvision

In [0]:
!pip3 install -q pytorch-pretrained-bert

In [0]:
# Download glue data.
! test -d download_glue_repo || git clone https://gist.github.com/60c2bdb54d156a41194446737ce03e2e.git download_glue_repo
!python download_glue_repo/download_glue_data.py --data_dir='glue_data' --tasks=$TASK

TASK_DATA_DIR = 'glue_data/' + TASK
print('***** Task data directory: {} *****'.format(TASK_DATA_DIR))
!ls $TASK_DATA_DIR

Cloning into 'download_glue_repo'...
remote: Enumerating objects: 21, done.
remote: Total 21 (delta 0), reused 0 (delta 0), pack-reused 21
Unpacking objects: 100% (21/21), done.
Traceback (most recent call last):
  File "download_glue_repo/download_glue_data.py", line 141, in <module>
    sys.exit(main(sys.argv[1:]))
  File "download_glue_repo/download_glue_data.py", line 129, in main
    tasks = get_tasks(args.tasks)
  File "download_glue_repo/download_glue_data.py", line 114, in get_tasks
    assert task_name in TASKS, "Task %s not found!" % task_name
AssertionError: Task  not found!


NameError: ignored

In [0]:
import pandas as pd
import os
import numpy as np
import pandas as pd
import zipfile
# from matplotlib import pyplot as plt
# %matplotlib inline
import sys
import datetime
import json
import torch

In [0]:
#downloading weights and cofiguration file for the model
!wget https://storage.googleapis.com/bert_models/2018_10_18/uncased_L-12_H-768_A-12.zip

--2019-04-23 14:22:48--  https://storage.googleapis.com/bert_models/2018_10_18/uncased_L-12_H-768_A-12.zip
Resolving storage.googleapis.com (storage.googleapis.com)... 173.194.69.128, 2a00:1450:4013:c04::80
Connecting to storage.googleapis.com (storage.googleapis.com)|173.194.69.128|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 407727028 (389M) [application/zip]
Saving to: ‘uncased_L-12_H-768_A-12.zip’

uncased_L-12_H-768_ 100%[===================>] 388.84M   139MB/s    in 2.8s    

2019-04-23 14:22:51 (139 MB/s) - ‘uncased_L-12_H-768_A-12.zip’ saved [407727028/407727028]



In [0]:
repo = 'model_repo'
with zipfile.ZipFile("uncased_L-12_H-768_A-12.zip","r") as zip_ref:
    zip_ref.extractall(repo)

In [71]:
# Available pretrained model checkpoints:
#   uncased_L-12_H-768_A-12: uncased BERT base model
#   uncased_L-24_H-1024_A-16: uncased BERT large model
#   cased_L-12_H-768_A-12: cased BERT large model
#We will use the most basic of all of them
BERT_MODEL = 'uncased_L-12_H-768_A-12'
BERT_PRETRAINED_DIR = f'{repo}/uncased_L-12_H-768_A-12'
OUTPUT_DIR = f'{repo}/outputs'

MODEL_NAME = 'bert-base-uncased'
print(f'***** Model output directory: {OUTPUT_DIR} *****')
print(f'***** BERT pretrained directory: {BERT_PRETRAINED_DIR} *****')

***** Model output directory: model_repo/outputs *****
***** BERT pretrained directory: model_repo/uncased_L-12_H-768_A-12 *****


In [0]:
# assert 'COLAB_TPU_ADDR' in os.environ, 'ERROR: Not connected to a TPU runtime; please see the first cell in this notebook for instructions!'
# TPU_ADDRESS = 'grpc://' + os.environ['COLAB_TPU_ADDR']
# print('TPU address is', TPU_ADDRESS)

from google.colab import auth
auth.authenticate_user()
# with tf.Session(TPU_ADDRESS) as session:
#   print('TPU devices:')
#   pprint.pprint(session.list_devices())

#   # Upload credentials to TPU.
#   with open('/content/adc.json', 'r') as f:
#     auth_info = json.load(f)
#   tf.contrib.cloud.configure_gcs(session, credentials=auth_info)
#   # Now credentials are set for all future sessions on this TPU.

NameError: ignored

In [70]:
BUCKET = 'bert-tre' #@param {type:"string"}
assert BUCKET, 'Must specify an existing GCS bucket name'
BUCKET_OUTPUT_DIR = 'gs://{}/bert_squad/outputs'.format(BUCKET)
print('***** Model output directory: {} *****'.format(OUTPUT_DIR))

***** Model output directory: gs://bert-tre/bert_squad/outputs *****


CommandException: The mb command requires a URL that specifies a bucket.
"gs://bert-tre/bert-squad" is not valid.


In [0]:
!wget https://raw.githubusercontent.com/xyz-zy/bert-temporal-relation-extraction/master/run_squad.py

--2019-04-23 14:22:57--  https://raw.githubusercontent.com/xyz-zy/bert-temporal-relation-extraction/master/run_squad.py
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 151.101.0.133, 151.101.64.133, 151.101.128.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|151.101.0.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 50654 (49K) [text/plain]
Saving to: ‘run_squad.py’

run_squad.py        100%[===================>]  49.47K  --.-KB/s    in 0.008s  

2019-04-23 14:22:57 (6.36 MB/s) - ‘run_squad.py’ saved [50654/50654]



In [0]:
!wget https://rajpurkar.github.io/SQuAD-explorer/dataset/train-v1.1.json
!wget https://rajpurkar.github.io/SQuAD-explorer/dataset/dev-v1.1.json
!wget https://github.com/allenai/bi-att-flow/blob/master/squad/evaluate-v1.1.py
!ls

--2019-04-23 14:22:59--  https://rajpurkar.github.io/SQuAD-explorer/dataset/train-v1.1.json
Resolving rajpurkar.github.io (rajpurkar.github.io)... 185.199.109.153, 185.199.110.153, 185.199.108.153, ...
Connecting to rajpurkar.github.io (rajpurkar.github.io)|185.199.109.153|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 30288272 (29M) [application/json]
Saving to: ‘train-v1.1.json’

train-v1.1.json     100%[===================>]  28.88M  --.-KB/s    in 0.1s    

2019-04-23 14:23:00 (198 MB/s) - ‘train-v1.1.json’ saved [30288272/30288272]

--2019-04-23 14:23:01--  https://rajpurkar.github.io/SQuAD-explorer/dataset/dev-v1.1.json
Resolving rajpurkar.github.io (rajpurkar.github.io)... 185.199.109.153, 185.199.110.153, 185.199.108.153, ...
Connecting to rajpurkar.github.io (rajpurkar.github.io)|185.199.109.153|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 4854279 (4.6M) [application/json]
Saving to: ‘dev-v1.1.json’

dev-v1.1.json       1

In [0]:
from torch.utils.data import (DataLoader, RandomSampler, SequentialSampler,
                              TensorDataset)

import pytorch_pretrained_bert
from pytorch_pretrained_bert.tokenization import BertTokenizer
from pytorch_pretrained_bert.optimization import BertAdam
from pytorch_pretrained_bert.modeling import BertForQuestionAnswering
from pytorch_pretrained_bert import file_utils
import run_squad

In [0]:
squad_train_examples = run_squad.read_squad_examples('train-v1.1.json', True, False)

In [0]:
squad_train_examples[0]

qas_id: 5733be284776f41900661182, question_text: To whom did the Virgin Mary allegedly appear in 1858 in Lourdes France?, doc_tokens: [Architecturally, the school has a Catholic character. Atop the Main Building's gold dome is a golden statue of the Virgin Mary. Immediately in front of the Main Building and facing it, is a copper statue of Christ with arms upraised with the legend "Venite Ad Me Omnes". Next to the Main Building is the Basilica of the Sacred Heart. Immediately behind the basilica is the Grotto, a Marian place of prayer and reflection. It is a replica of the grotto at Lourdes, France where the Virgin Mary reputedly appeared to Saint Bernadette Soubirous in 1858. At the end of the main drive (and in a direct line that connects through 3 statues and the Gold Dome), is a simple, modern stone statue of Mary.], start_position: 90, end_position: 92

In [0]:
tokenizer = BertTokenizer.from_pretrained(MODEL_NAME, do_lower_case=True)

100%|██████████| 231508/231508 [00:00<00:00, 915225.53B/s]


In [0]:
tokenizer.tokenize(squad_train_examples[0].question_text)

['to',
 'whom',
 'did',
 'the',
 'virgin',
 'mary',
 'allegedly',
 'appear',
 'in',
 '1858',
 'in',
 'lou',
 '##rdes',
 'france',
 '?']

In [0]:
# Model Hyper Parameters
TRAIN_BATCH_SIZE = 32
EVAL_BATCH_SIZE = 16
PREDICT_BATCH_SIZE = 8
LEARNING_RATE = 2e-5
NUM_TRAIN_EPOCHS = 1.0
WARMUP_PROPORTION = 0.1
GRADIENT_ACCUMULATION_STEPS = 1
MAX_SEQ_LENGTH = 128
DOC_STRIDE=128
MAX_QUERY_LENGTH=64
LOCAL_RANK = -1
N_BEST_SIZE = 20
MAX_ANSWER_LENGTH = 30
VERSION_2_WITH_NEGATIVE = False
NULL_SCORE_DIFF_THRESHOLD = 0.0
# Model configs
SAVE_CHECKPOINTS_STEPS = 1000 #if you wish to finetune a model on a larger dataset, use larger interval
# each checpoint weights about 1,5gb
ITERATIONS_PER_LOOP = 1000
NUM_TPU_CORES = 8
VOCAB_FILE = os.path.join(BERT_PRETRAINED_DIR, 'vocab.txt')
CONFIG_FILE = os.path.join(BERT_PRETRAINED_DIR, 'bert_config.json')
INIT_CHECKPOINT = os.path.join(BERT_PRETRAINED_DIR, 'bert_model.ckpt')
DO_LOWER_CASE = BERT_MODEL.startswith('uncased')

In [0]:
num_train_optimization_steps = int(len(squad_train_examples) / TRAIN_BATCH_SIZE / GRADIENT_ACCUMULATION_STEPS) * NUM_TRAIN_EPOCHS

In [0]:
model = BertForQuestionAnswering.from_pretrained(MODEL_NAME,
                cache_dir=os.path.join(str(file_utils.PYTORCH_PRETRAINED_BERT_CACHE), 'distributed_{}'.format(-1)))

100%|██████████| 407873900/407873900 [00:14<00:00, 29132585.38B/s]


In [0]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
n_gpu = torch.cuda.device_count()
print(device, n_gpu)

In [0]:
model.to(device)

BertForQuestionAnswering(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): BertLayerNorm()
      (dropout): Dropout(p=0.1)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): BertLayerNorm()
              (dropout): Dropout(p=0.1)
            )
          )
          (intermediate): BertIntermediate

In [0]:
# Prepare optimizer
param_optimizer = list(model.named_parameters())

# hack to remove pooler, which is not used
# thus it produce None grad that break apex
param_optimizer = [n for n in param_optimizer if 'pooler' not in n[0]]

no_decay = ['bias', 'LayerNorm.bias', 'LayerNorm.weight']
optimizer_grouped_parameters = [
    {'params': [p for n, p in param_optimizer if not any(nd in n for nd in no_decay)], 'weight_decay': 0.01},
    {'params': [p for n, p in param_optimizer if any(nd in n for nd in no_decay)], 'weight_decay': 0.0}
    ]

In [0]:
optimizer = BertAdam(optimizer_grouped_parameters,
                   lr=LEARNING_RATE,
                   warmup=WARMUP_PROPORTION,
                   t_total=num_train_optimization_steps)

In [0]:
train_features = run_squad.convert_examples_to_features(
            examples=squad_train_examples,
            tokenizer=tokenizer,
            max_seq_length=MAX_SEQ_LENGTH,
            doc_stride=DOC_STRIDE,
            max_query_length=MAX_QUERY_LENGTH,
            is_training=True)

In [0]:
train_features[0]

In [0]:
from torch.utils.data import DataLoader, TensorDataset, RandomSampler
all_input_ids = torch.tensor([f.input_ids for f in train_features], dtype=torch.long)
all_input_mask = torch.tensor([f.input_mask for f in train_features], dtype=torch.long)
all_segment_ids = torch.tensor([f.segment_ids for f in train_features], dtype=torch.long)
all_start_positions = torch.tensor([f.start_position for f in train_features], dtype=torch.long)
all_end_positions = torch.tensor([f.end_position for f in train_features], dtype=torch.long)
train_data = TensorDataset(all_input_ids, all_input_mask, all_segment_ids,
                           all_start_positions, all_end_positions)

train_sampler = RandomSampler(train_data)

In [0]:
train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size=TRAIN_BATCH_SIZE)

In [0]:
model.train()

BertForQuestionAnswering(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): BertLayerNorm()
      (dropout): Dropout(p=0.1)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): BertLayerNorm()
              (dropout): Dropout(p=0.1)
            )
          )
          (intermediate): BertIntermediate

In [0]:
from tqdm import tqdm, trange
global_step = 0
for _ in trange(int(NUM_TRAIN_EPOCHS), desc="Epoch"):
    for step, batch in enumerate(tqdm(train_dataloader, desc="Iteration", disable=LOCAL_RANK not in [-1, 0])):
        if n_gpu == 1:
          batch = tuple(t.to(device) for t in batch) # multi-gpu does scattering it-self
        input_ids, input_mask, segment_ids, start_positions, end_positions = batch
        loss = model(input_ids, segment_ids, input_mask, start_positions, end_positions)
        if n_gpu > 1:
            loss = loss.mean() # mean() to average on multi-gpu.
        if GRADIENT_ACCUMULATION_STEPS > 1:
            loss = loss / GRADIENT_ACCUMULATION_STEPS

#         if args.fp16:
#             optimizer.backward(loss)
#         else:
        loss.backward()
        print("%s" % loss)
        if (step + 1) % GRADIENT_ACCUMULATION_STEPS == 0:
#             if args.fp16:
#                 # modify learning rate with special warm up BERT uses
#                 # if args.fp16 is False, BertAdam is used and handles this automatically
#                 lr_this_step = args.learning_rate * warmup_linear(global_step/num_train_optimization_steps, args.warmup_proportion)
#                 for param_group in optimizer.param_groups:
#                     param_group['lr'] = lr_this_step
            optimizer.step()
            optimizer.zero_grad()
            global_step += 1

Iteration:   0%|          | 1/5217 [00:01<1:32:21,  1.06s/it]

tensor(4.8483, device='cuda:0', grad_fn=<DivBackward0>)



Iteration:   0%|          | 2/5217 [00:01<1:26:58,  1.00s/it]

tensor(4.7906, device='cuda:0', grad_fn=<DivBackward0>)



Iteration:   0%|          | 3/5217 [00:02<1:23:23,  1.04it/s]

...

tensor(95.0970, device='cuda:0', grad_fn=<DivBackward0>)



Iteration: 100%|█████████▉| 5216/5217 [1:17:21<00:00,  1.13it/s]

tensor(91.9771, device='cuda:0', grad_fn=<DivBackward0>)



Epoch: 100%|██████████| 3/3 [3:51:54<00:00, 4638.01s/it]  

tensor(94.4462, device='cuda:0', grad_fn=<DivBackward0>)


In [0]:
# Save a trained model, configuration and tokenizer
model_to_save = model.module if hasattr(model, 'module') else model  # Only save the model it-self

In [0]:
def to_json_file(config, json_file_path):
        """ Save this instance to a json file."""
        with open(json_file_path, "w", encoding='utf-8') as writer:
            writer.write(config.to_json_string())

In [0]:
def save_vocabulary(tokenizer, vocab_path):
    """Save the tokenizer vocabulary to a directory or file."""
    index = 0
    if os.path.isdir(vocab_path):
        vocab_file = os.path.join(vocab_path, 'vocab.txt')
    with open(vocab_file, "w", encoding="utf-8") as writer:
        for token, token_index in sorted(tokenizer.vocab.items(), key=lambda kv: kv[1]):
            if index != token_index:
                logger.warning("Saving vocabulary to {}: vocabulary indices are not consecutive."
                               " Please check that the vocabulary is not corrupted!".format(vocab_file))
                index = token_index
            writer.write(token + u'\n')
            index += 1
    return vocab_file

In [0]:
if not os.path.exists(OUTPUT_DIR):
    os.makedirs(OUTPUT_DIR)

In [76]:
# If we save using the predefined names, we can load using `from_pretrained`

output_model_file = os.path.join(OUTPUT_DIR, "pytorch_model.bin")
output_config_file = os.path.join(OUTPUT_DIR, "bert_config.json")

torch.save(model_to_save.state_dict(), output_model_file)
to_json_file(model_to_save.config, output_config_file)
#model_to_save.config.to_json_file(output_config_file)
save_vocabulary(tokenizer, OUTPUT_DIR)#tokenizer.save_vocabulary(OUTPUT_DIR)

'model_repo/outputs/vocab.txt'

In [102]:
!gsutil cp ./model_repo/outputs/* gs://bert-tre/bert_squad/outputs/

Copying file://./model_repo/outputs/bert_config.json [Content-Type=application/json]...
Copying file://./model_repo/outputs/nbest_predictions.json [Content-Type=application/json]...
Copying file://./model_repo/outputs/predictions.json [Content-Type=application/json]...
Copying file://./model_repo/outputs/pytorch_bert.bin [Content-Type=application/octet-stream]...
==> NOTE: You are uploading one or more large file(s), which would run
significantly faster if you enable parallel composite uploads. This
feature can be enabled by editing the
"parallel_composite_upload_threshold" value in your .boto
configuration file. However, note that if you do this large files will
be uploaded as `composite objects
<https://cloud.google.com/storage/docs/composite-objects>`_,which
means that any user who downloads such objects will need to have a
compiled crcmod installed (see "gsutil help crcmod"). This is because
without a compiled crcmod, computing checksums on composite objects is
so slow that gsutil 

#Evaluate Model

In [0]:
# Load a trained model and vocabulary that you have fine-tuned
model = BertForQuestionAnswering.from_pretrained(OUTPUT_DIR)
tokenizer = BertTokenizer.from_pretrained(OUTPUT_DIR, do_lower_case=DO_LOWER_CASE)

In [79]:
model.to(device)

BertForQuestionAnswering(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): BertLayerNorm()
      (dropout): Dropout(p=0.1)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): BertLayerNorm()
              (dropout): Dropout(p=0.1)
            )
          )
          (intermediate): BertIntermediate

In [0]:
eval_examples = run_squad.read_squad_examples(
    input_file="dev-v1.1.json", is_training=False, version_2_with_negative=False)
eval_features = run_squad.convert_examples_to_features(
    examples=eval_examples,
    tokenizer=tokenizer,
    max_seq_length=MAX_SEQ_LENGTH,
    doc_stride=DOC_STRIDE,
    max_query_length=MAX_QUERY_LENGTH,
    is_training=False)

In [0]:
all_input_ids = torch.tensor([f.input_ids for f in eval_features], dtype=torch.long)
all_input_mask = torch.tensor([f.input_mask for f in eval_features], dtype=torch.long)
all_segment_ids = torch.tensor([f.segment_ids for f in eval_features], dtype=torch.long)
all_example_index = torch.arange(all_input_ids.size(0), dtype=torch.long)
eval_data = TensorDataset(all_input_ids, all_input_mask, all_segment_ids, all_example_index)
# Run prediction for full data
eval_sampler = SequentialSampler(eval_data)
eval_dataloader = DataLoader(eval_data, sampler=eval_sampler, batch_size=PREDICT_BATCH_SIZE)

In [104]:
model.eval()
all_results = []
print("Start evaluating")
for input_ids, input_mask, segment_ids, example_indices in tqdm(eval_dataloader, desc="Evaluating", disable=LOCAL_RANK not in [-1, 0]):
    if len(all_results) % 1000 == 0:
        print("Processing example: %d" % (len(all_results)))
    input_ids = input_ids.to(device)
    input_mask = input_mask.to(device)
    segment_ids = segment_ids.to(device)
    with torch.no_grad():
        batch_start_logits, batch_end_logits = model(input_ids, segment_ids, input_mask)
    for i, example_index in enumerate(example_indices):
        start_logits = batch_start_logits[i].detach().cpu().tolist()
        end_logits = batch_end_logits[i].detach().cpu().tolist()
        eval_feature = eval_features[example_index.item()]
        unique_id = int(eval_feature.unique_id)
        all_results.append(run_squad.RawResult(unique_id=unique_id,
                                     start_logits=start_logits,
                                     end_logits=end_logits))

Evaluating:   0%|          | 1/2599 [00:00<04:24,  9.83it/s]

Start evaluating
Processing example: 0


Evaluating:   5%|▍         | 126/2599 [00:08<02:53, 14.25it/s]

Processing example: 1000


Evaluating:  10%|▉         | 252/2599 [00:17<02:49, 13.88it/s]

...

Evaluating:  91%|█████████▏| 2376/2599 [02:55<00:16, 13.60it/s]

Processing example: 19000


Evaluating:  96%|█████████▋| 2502/2599 [03:04<00:07, 13.57it/s]

Processing example: 20000


Evaluating: 100%|██████████| 2599/2599 [03:11<00:00, 13.57it/s]


In [0]:
output_prediction_file = os.path.join(OUTPUT_DIR, "predictions.json")
output_nbest_file = os.path.join(OUTPUT_DIR, "nbest_predictions.json")
output_null_log_odds_file = os.path.join(OUTPUT_DIR, "null_odds.json")
run_squad.write_predictions(eval_examples, eval_features, all_results,
                  N_BEST_SIZE, MAX_ANSWER_LENGTH,
                  DO_LOWER_CASE, output_prediction_file,
                  output_nbest_file, output_null_log_odds_file, False,
                  VERSION_2_WITH_NEGATIVE, NULL_SCORE_DIFF_THRESHOLD)